In [2]:
import pylab, random
from rcParamsSettings import *

# 以下の関数はこれ以前の章で定義されているもので，
# この章で利用する．
def stdDev(X):
    """X を数のリストとする
       X の標準偏差を出力する"""
    mean = float(sum(X))/len(X)
    tot = 0.0
    for x in X:
        tot += (x - mean)**2
    return (tot/len(X))**0.5 # 平均との差の 2 乗根

def CV(X):
    mean = sum(X)/float(len(X))
    try:
        return stdDev(X)/mean
    except ZeroDivisionError:
        return float('nan')


In [3]:
#Page 201, Figure 13.1
class Location(object):
    #
    def __init__(self, x, y):
        """x と y は浮動小数点数"""
        self.x = x
        self.y = y
    #
    def move(self, deltaX, deltaY):
        """deltaX と deltaY は浮動小数点数"""
        return Location(self.x + deltaX, self.y + deltaY)
    #
    def getX(self):
        return self.x
    #
    def getY(self):
        return self.y
    #
    def distFrom(self, other):
        ox = other.x
        oy = other.y
        xDist = self.x - ox
        yDist = self.y - oy
        return (xDist**2 + yDist**2)**0.5
    #
    def __str__(self):
        return '<' + str(self.x) + ', ' + str(self.y) + '>'


In [4]:
#Page 202, Figure 13.2
class Field(object):
    #    
    def __init__(self):
        self.drunks = {}
    #            
    def addDrunk(self, drunk, loc):
        if drunk in self.drunks:
            raise ValueError('Duplicate drunk')
        else:
            self.drunks[drunk] = loc
    #                
    def moveDrunk(self, drunk):
        if drunk not in self.drunks:
            raise ValueError('Drunk not in field')
        xDist, yDist = drunk.takeStep()
        currentLocation = self.drunks[drunk]
        # Location クラスの move メソッドを用いて，新しい位置情報を得る
        self.drunks[drunk] = currentLocation.move(xDist, yDist)
    #            
    def getLoc(self, drunk):
        if drunk not in self.drunks:
            raise ValueError('Drunk not in field')
        return self.drunks[drunk]


In [5]:
#Page 202, Figure 13.3
class Drunk(object):
    def __init__(self, name = None):
        """name を文字列とする"""
        self.name = name
    #    
    def __str__(self):
        if self != None:
            return self.name
        return 'Anonymous'

class UsualDrunk(Drunk):
    def takeStep(self):
        stepChoices = [(0.0,1.0), (0.0,-1.0), (1.0, 0.0), (-1.0, 0.0)]
        return random.choice(stepChoices)


In [6]:
#Page 203, Figure 13.4
def walk(f, d, numSteps):
    """f: Field クラスのオブジェクト
       d: Drunk クラスのオブジェクト
       numSteps: 0 以上の整数
       d を numSteps 回移動し，酔歩の初期位置と最終位置との差を出力する"""
    start = f.getLoc(d)
    for s in range(numSteps):
        f.moveDrunk(d)
    return start.distFrom(f.getLoc(d))

def simWalks(numSteps, numTrials, dClass):
    """numSteps: 0 以上の整数
       numTrials: 正の整数
       dClass: Drunk のサブクラス
       numSteps 回移動する酔歩を，numTrials 回シミュレートする．
       各実験の初期位置と最終位置との差をリストにして出力する"""
    Homer = dClass()
    origin = Location(0.0, 0.0)
    distances = []
    for t in range(numTrials):
        f = Field()
        f.addDrunk(Homer, origin)
        distances.append(walk(f, Homer, numTrials))  # bug
    return distances

def drunkTest(walkLengths, numTrials, dClass):
    """walkLengths: 0 以上の整数のシークエンス
       numTrials: 正の整数
       dClass: Drunk のサブクラス
       walkLengths の各要素を酔歩の移動回数として, numTrials 回の酔歩を
       シミュレートする simWalks を実行し，結果を出力する"""
    for numSteps in walkLengths:
        distances = simWalks(numSteps, numTrials, dClass)
        print( dClass.__name__, 'random walk of', numSteps, 'steps')
        print( ' Mean =', sum(distances)/len(distances),
              'CV =', CV(distances))
        print( ' Max =', max(distances), 'Min =', min(distances))


In [7]:
#Page 204
drunkTest((10,100,1000,10000),100,UsualDrunk)

drunkTest((0,1),100,UsualDrunk)


UsualDrunk random walk of 10 steps
 Mean = 8.729382119498247 CV = 0.498256322334708
 Max = 21.2602916254693 Min = 1.4142135623730951
UsualDrunk random walk of 100 steps
 Mean = 9.65153422234427 CV = 0.46622279211256695
 Max = 22.135943621178654 Min = 1.4142135623730951
UsualDrunk random walk of 1000 steps
 Mean = 8.498794179056974 CV = 0.5801490848481212
 Max = 22.360679774997898 Min = 0.0
UsualDrunk random walk of 10000 steps
 Mean = 8.454537623534032 CV = 0.5914077835169597
 Max = 26.419689627245813 Min = 0.0
UsualDrunk random walk of 0 steps
 Mean = 8.443360288834594 CV = 0.5563941676896587
 Max = 23.194827009486403 Min = 1.4142135623730951
UsualDrunk random walk of 1 steps
 Mean = 8.7119799581849 CV = 0.518203323535595
 Max = 24.166091947189145 Min = 1.4142135623730951


In [8]:
def simWalks(numSteps, numTrials, dClass):
    """numSteps: 0 以上の整数
       numTrials: 正の整数
       dClass: Drunk のサブクラス
       numSteps 回移動する酔歩を，numTrials 回シミュレートする．
       各実験の初期位置と最終位置との差をリストにして出力する"""
    Homer = dClass()
    origin = Location(0.0, 0.0)
    distances = []
    for t in range(numTrials):
        f = Field()
        f.addDrunk(Homer, origin)
        distances.append(walk(f, Homer, numSteps))
    return distances

#Page 206, Figure 13.5
class ColdDrunk(Drunk):
    def takeStep(self):
        stepChoices = [(0.0,1.0), (0.0,-2.0), (1.0, 0.0), (-1.0, 0.0)]
        return random.choice(stepChoices)

class EWDrunk(Drunk):
    def takeStep(self):
        stepChoices = [(1.0, 0.0), (-1.0, 0.0)]
        return random.choice(stepChoices) 

def simAll(drunkKinds, walkLengths, numTrials):
    for dClass in drunkKinds:
        drunkTest(walkLengths, numTrials, dClass)

simAll((UsualDrunk, ColdDrunk, EWDrunk), (100,1000), 10)


UsualDrunk random walk of 100 steps
 Mean = 8.233132789750524 CV = 0.48910305989947034
 Max = 17.204650534085253 Min = 4.47213595499958
UsualDrunk random walk of 1000 steps
 Mean = 28.89185587059946 CV = 0.4174431545889083
 Max = 49.57822102496216 Min = 10.198039027185569
ColdDrunk random walk of 100 steps
 Mean = 23.696940457309978 CV = 0.19682823400759822
 Max = 30.59411708155671 Min = 15.524174696260024
ColdDrunk random walk of 1000 steps
 Mean = 259.68121518714435 CV = 0.12386815096888129
 Max = 311.46428366668306 Min = 209.02152999152983
EWDrunk random walk of 100 steps
 Mean = 6.4 CV = 0.5376453291901642
 Max = 12.0 Min = 0.0
EWDrunk random walk of 1000 steps
 Mean = 28.2 CV = 0.5954490992497125
 Max = 64.0 Min = 8.0


In [9]:
#Page 207, Figure 13.6
class styleIterator(object):
    def __init__(self, styles):
        self.index = 0
        self.styles = styles
    #
    def nextStyle(self):
        result = self.styles[self.index]
        if self.index == len(self.styles) - 1:
            self.index = 0
        else:
            self.index += 1
        return result


In [10]:
#Page 207-208, Figure 13.7
def simDrunk(numTrials, dClass, walkLengths):
    meanDistances = []
    cvDistances = []
    for numSteps in walkLengths:
        print( 'Starting simulation of', numSteps, 'steps')
        trials = simWalks(numSteps, numTrials, dClass)
        mean = sum(trials)/float(len(trials))
        meanDistances.append(mean)
        cvDistances.append(stdDev(trials)/mean)
    return (meanDistances, cvDistances)

def simAll(drunkKinds, walkLengths, numTrials):
    styleChoice = styleIterator(('b-', 'r:', 'm-.'))
    for dClass in drunkKinds:
        curStyle = styleChoice.nextStyle()
        print( 'Starting simulation of', dClass.__name__)
        means, cvs = simDrunk(numTrials, dClass, walkLengths)
        cvMean = sum(cvs)/float(len(cvs))
        pylab.plot(walkLengths, means, curStyle,
                   label = dClass.__name__ +
                          '(CV = ' + str(round(cvMean, 4)) + ')')
    pylab.title('Mean Distance from Origin ('
                + str(numTrials) + ' trials)')
    pylab.xlabel('Number of Steps')
    pylab.ylabel('Distance from Origin')
    pylab.legend(loc = 'best')
    pylab.semilogx()
    pylab.semilogy()

simAll((UsualDrunk, ColdDrunk, EWDrunk), (10,100,1000,10000,100000), 100)


Starting simulation of UsualDrunk
Starting simulation of 10 steps
Starting simulation of 100 steps
Starting simulation of 1000 steps
Starting simulation of 10000 steps
Starting simulation of 100000 steps
Starting simulation of ColdDrunk
Starting simulation of 10 steps
Starting simulation of 100 steps
Starting simulation of 1000 steps
Starting simulation of 10000 steps
Starting simulation of 100000 steps
Starting simulation of EWDrunk
Starting simulation of 10 steps
Starting simulation of 100 steps
Starting simulation of 1000 steps
Starting simulation of 10000 steps
Starting simulation of 100000 steps


In [12]:
#Page 209, Figure 13.8
def getFinalLocs(numSteps, numTrials, dClass):
    locs = []
    d = dClass()
    origin = Location(0, 0)
    for t in range(numTrials):
        f = Field()
        f.addDrunk(d, origin)
        for s in range(numSteps):
            f.moveDrunk(d)
        locs.append(f.getLoc(d))
    return locs

def plotLocs(drunkKinds, numSteps, numTrials):
    styleChoice = styleIterator(('b+', 'r^', 'mo'))
    for dClass in drunkKinds:
        locs = getFinalLocs(numSteps, numTrials, dClass)
        xVals, yVals = [], []
        for l in locs:
            xVals.append(l.getX())
            yVals.append(l.getY())
        meanX = sum(xVals)/float(len(xVals))
        meanY = sum(yVals)/float(len(yVals))
        curStyle = styleChoice.nextStyle()
        pylab.plot(xVals, yVals, curStyle,
                      label = dClass.__name__ + ' Mean loc. = <'
                      + str(meanX) + ', ' + str(meanY) + '>')
    pylab.title('Location at End of Walks ('
                + str(numSteps) + ' steps)')
    pylab.xlabel('Steps East/West of Origin')
    pylab.ylabel('Steps North/South of Origin')
    pylab.legend(loc = 'lower left', numpoints = 1)

plotLocs((UsualDrunk, ColdDrunk, EWDrunk), 100, 200)


In [13]:
pylab.show()

In [18]:
#Page 190, Figure 13.9
def traceWalk(drunkKinds, numSteps):
    styleChoice = styleIterator(('b+', 'r^', 'mo'))
    f = Field()
    for dClass in drunkKinds:
        d = dClass()
        f.addDrunk(d, Location(0, 0))
        locs = []
        for s in range(numSteps):
            f.moveDrunk(d)
            locs.append(f.getLoc(d))
        xVals = []
        yVals = []
        for l in locs:
            xVals.append(l.getX())
            yVals.append(l.getY())
        curStyle = styleChoice.nextStyle()
        pylab.plot(xVals, yVals, curStyle,
                   label = dClass.__name__)
    pylab.title('Spots Visited on Walk ('
                + str(numSteps) + ' steps)')
    pylab.xlabel('Steps East/West of Origin')
    pylab.ylabel('Steps North/South of Origin')
    pylab.legend(loc = 'best')

traceWalk((UsualDrunk, ColdDrunk, EWDrunk), 200)


In [19]:
pylab.show()

In [16]:
#Page 192, Figure 13.10
class oddField(Field):
    def __init__(self, numHoles, xRange, yRange):
        Field.__init__(self)
        self.wormholes = {}
        for w in range(numHoles):
            x = random.randint(-xRange, xRange)
            y = random.randint(-yRange, yRange)
            newX = random.randint(-xRange, xRange)
            newY = random.randint(-yRange, yRange)
            newLoc = Location(newX, newY)
            self.wormholes[(x, y)] = newLoc
    #
    def moveDrunk(self, drunk):
        Field.moveDrunk(self, drunk)
        x = self.drunks[drunk].getX()
        y = self.drunks[drunk].getY()
        if (x, y) in self.wormholes:
            self.drunks[drunk] = self.wormholes[(x, y)]

def traceWalk(drunkKinds, numSteps):
    styleChoice = styleIterator(('b+', 'r^', 'mo'))
    f = oddField(1000,100,200)	# modified
    for dClass in drunkKinds:
        d = dClass()
        f.addDrunk(d, Location(0, 0))
        locs = []
        for s in range(numSteps):
            f.moveDrunk(d)
            locs.append(f.getLoc(d))
        xVals = []
        yVals = []
        for l in locs:
            xVals.append(l.getX())
            yVals.append(l.getY())
        curStyle = styleChoice.nextStyle()
        pylab.plot(xVals, yVals, curStyle,
                   label = dClass.__name__)
    pylab.title('Spots Visited on Walk ('
                + str(numSteps) + ' steps)')
    pylab.xlabel('Steps East/West of Origin')
    pylab.ylabel('Steps North/South of Origin')
    pylab.legend(loc = 'best')

traceWalk((UsualDrunk, ColdDrunk, EWDrunk), 200)


In [20]:
pylab.show()